### Configuring spark and Azure Data Lake Storage

In [0]:
from pyspark.sql import SparkSession

# Initialize Spark Session
spark = SparkSession.builder \
    .appName("Delta Lake ETL") \
    .config("spark.sql.extensions", "io.delta.sql.DeltaSparkSessionExtension") \
    .config("spark.sql.catalog.spark_catalog", "org.apache.spark.sql.delta.catalog.DeltaCatalog") \
    .getOrCreate()

# Configure ADLS access
storage_account_name = "<azure_storage_account_name>"
storage_account_key = "<azure_storage_account_key>"
container_name = "<azure_container_name>"

spark.conf.set(f"fs.azure.account.key.{storage_account_name}.dfs.core.windows.net", storage_account_key)

### Defining bronze, silver paths

In [0]:
# Define paths
adls_path = f"abfss://{container_name}@{storage_account_name}.dfs.core.windows.net"
bronze_path = f"{adls_path}/bronze"
silver_path = f"{adls_path}/silver"

### Create silver_db database

In [0]:
# Create database for Silver layer
spark.sql("CREATE DATABASE IF NOT EXISTS silver_db")
spark.sql("USE silver_db")

Out[3]: DataFrame[]

In this Silver Layer, we store data in "Delta Lake" format.

- Delta Lake = Parquet + Transaction Logs

- Enables ACID compliance for Big Data Storage

#### Note: Data gets stored in ADLS but it is exposed as a table in Databricks.


- Read Promotions from ADLS Bronze Layer

In [0]:
promotions_bronze = spark.read.parquet(bronze_path + '/promotions/*.parquet')

promotions_bronze.createOrReplaceTempView('promotions_bronze')

In [0]:
%sql

SELECT *,
      CASE 
          WHEN datediff(end_date, start_date) <= 7 THEN 'Short-term'
          WHEN datediff(end_date, start_date) <= 30 THEN 'Medium-term'
          ELSE 'Long-term'
      END AS promotion_duration
    FROM promotions_bronze

promotion_id name description discount_type discount_value start_date end_date promotion_duration ec7693b5-6288-4e89-b976-2a8dda4a1efd Organic content-based support Chance parent generation whose network voice few. Percentage 49.59 2025-01-10 2025-01-19 Medium-term 2fabef52-ebb1-43fb-8b82-98d6bd568812 Programmable impactful benchmark Weight at manage operation far court. Boy require we. Fixed Amount 12.01 2025-02-12 2025-03-10 Medium-term 5952a89e-26c0-44af-985e-2de13f35d83a Expanded non-volatile orchestration Fly end person front value. On record its anyone exist information only. Fixed Amount 40.21 2025-01-15 2025-01-19 Short-term 38fa7d12-a21d-4074-bed4-3048467c5d76 Ergonomic high-level algorithm Time effect education power according. Citizen control suffer husband building nice score. Rather fish not small realize so people. Percentage 5.00 2025-01-17 2025-01-18 Short-term a9064763-d11b-4f02-9e15-0d7e47019c92 Multi-tiered interactive framework Natural play bit allow popular lose better. Success about yeah option actually race west. Fixed Amount 10.00 2025-01-20 2025-01-29 Medium-term 45e8add0-0c04-42b0-ba08-983c6647482f Networked well-modulated migration Morning plant on keep. Whatever partner think listen sit. Simply ready continue American if day fill. Percentage 36.60 2025-01-03 2025-01-22 Medium-term 3901196c-1534-4faf-a775-daf5c913e794 Face-to-face value-added throughput Cost ball treat our. Fixed Amount 10.20 2025-01-26 2025-01-31 Short-term e6cc04cd-77b6-4256-82f1-7dffd9b24533 Virtual cohesive model Area million research pick. Drug analysis meet discussion specific consumer. Fixed Amount 10.00 2025-01-23 2025-02-06 Medium-term 7979a1e8-0e76-4532-b128-48d4a9353950 User-friendly fault-tolerant benchmark Table wish today cultural. Heart exactly voice compare form listen. Author here institution Mr lot. Percentage 10.51 2025-02-07 2025-02-28 Medium-term d110bb1f-82fb-433d-a770-7e3b98180b75 Multi-tiered radical knowledgebase Trade create see energy. Citizen position economy. Position meeting very product. Fixed Amount 24.09 2025-02-07 2025-02-23 Medium-term b56a339d-7819-4546-8a53-d22864e18472 Centralized object-oriented Graphic Interface Wind dog exactly scientist fill much. For his call firm remain. Fixed Amount 27.03 2025-02-07 2025-02-24 Medium-term 1a47f448-b65a-4174-8e26-169525a39e45 Object-based full-range policy Travel feel off onto star lead. Fixed Amount 46.72 2025-01-29 2025-02-23 Medium-term efbbe61f-05c0-4469-bf56-a6d326308e5b Self-enabling web-enabled initiative Career level down reach security director. Age fall eye three. Agreement adult within official certain difficult. Percentage 47.67 2025-01-25 2025-02-09 Medium-term ddc14a78-0065-461e-b8c7-cf70d58b61d9 Public-key solution-oriented alliance Wind require around region go letter always past. Seek community talk once buy tough. Room force blue upon father free. Fixed Amount 7.76 2025-01-29 2025-02-09 Medium-term 3a998737-105f-4c41-bc12-d1d51e85f331 Business-focused local migration Bad cost clearly difference social. Key company common chair. Percentage 11.20 2025-01-02 2025-01-26 Medium-term 3442db3f-c89b-4909-8d1f-63db334aa6d5 Polarized upward-trending core Prepare hotel decade chair with. Nothing thus citizen whatever operation rest. Watch federal upon prepare several speech. Fixed Amount 9.60 2025-02-02 2025-03-01 Medium-term 91527ba1-a6ac-48db-98c6-632573f3e4e0 Compatible object-oriented infrastructure Until himself surface public. Radio money memory those store move see. Democrat figure cell check participant. Fixed Amount 32.26 2025-02-08 2025-02-17 Medium-term d33c23ca-0910-482a-89d0-a424bd7ee7c9 User-centric object-oriented toolset Individual operation executive. Percentage 26.48 2025-02-05 2025-02-06 Short-term ad55558a-6303-466b-96a2-b27fa5962d5c Reverse-engineered impactful encryption East pass whether third. Across individual those big. Physical little west worker. Percentage 46.01 2025-01-23 2025-02-12 Medium-term 913f255c-8b48-4de4-9370-04

### Silver Layer Promotions

- Create a new column before finalizing Promotions Silver.
- Based on promotion period, decide if it is "Short-term", "Medium-term", or "Long-term"

In [0]:
# Process Silver layer
spark.sql(
            f"""
            CREATE OR REPLACE TABLE silver_db.silver_promotions
            USING DELTA
            LOCATION '{silver_path}/promotions'
            AS
                SELECT *,
                    CASE 
                        WHEN datediff(end_date, start_date) <= 7 THEN 'Short-term'
                        WHEN datediff(end_date, start_date) <= 30 THEN 'Medium-term'
                        ELSE 'Long-term'
                    END AS promotion_duration
                FROM parquet.`{bronze_path}/promotions/`
            """
)

Out[6]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
%sql

SELECT * FROM silver_db.silver_promotions LIMIT 10

promotion_id name description discount_type discount_value start_date end_date promotion_duration ec7693b5-6288-4e89-b976-2a8dda4a1efd Organic content-based support Chance parent generation whose network voice few. Percentage 49.59 2025-01-10 2025-01-19 Medium-term 2fabef52-ebb1-43fb-8b82-98d6bd568812 Programmable impactful benchmark Weight at manage operation far court. Boy require we. Fixed Amount 12.01 2025-02-12 2025-03-10 Medium-term 5952a89e-26c0-44af-985e-2de13f35d83a Expanded non-volatile orchestration Fly end person front value. On record its anyone exist information only. Fixed Amount 40.21 2025-01-15 2025-01-19 Short-term 38fa7d12-a21d-4074-bed4-3048467c5d76 Ergonomic high-level algorithm Time effect education power according. Citizen control suffer husband building nice score. Rather fish not small realize so people. Percentage 5.00 2025-01-17 2025-01-18 Short-term a9064763-d11b-4f02-9e15-0d7e47019c92 Multi-tiered interactive framework Natural play bit allow popular lose better. Success about yeah option actually race west. Fixed Amount 10.00 2025-01-20 2025-01-29 Medium-term 45e8add0-0c04-42b0-ba08-983c6647482f Networked well-modulated migration Morning plant on keep. Whatever partner think listen sit. Simply ready continue American if day fill. Percentage 36.60 2025-01-03 2025-01-22 Medium-term 3901196c-1534-4faf-a775-daf5c913e794 Face-to-face value-added throughput Cost ball treat our. Fixed Amount 10.20 2025-01-26 2025-01-31 Short-term e6cc04cd-77b6-4256-82f1-7dffd9b24533 Virtual cohesive model Area million research pick. Drug analysis meet discussion specific consumer. Fixed Amount 10.00 2025-01-23 2025-02-06 Medium-term 7979a1e8-0e76-4532-b128-48d4a9353950 User-friendly fault-tolerant benchmark Table wish today cultural. Heart exactly voice compare form listen. Author here institution Mr lot. Percentage 10.51 2025-02-07 2025-02-28 Medium-term d110bb1f-82fb-433d-a770-7e3b98180b75 Multi-tiered radical knowledgebase Trade create see energy. Citizen position economy. Position meeting very product. Fixed Amount 24.09 2025-02-07 2025-02-23 Medium-term

### Silver Layer Customers
- Calculate age for each customer

- Save it to silver customers table

In [0]:
spark.sql(f"""
        CREATE OR REPLACE TABLE silver_db.silver_customers
        USING DELTA
        LOCATION '{silver_path}/customers'
        AS
        SELECT *,
            datediff(current_date(), date_of_birth) / 365.25 AS age
        FROM parquet.`{bronze_path}/customers`
""")



Out[8]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

### Silver Layer Products

- Create a price category column : "Price Category"

In [0]:
spark.sql(f"""
            CREATE OR REPLACE TABLE silver_db.silver_products
            USING DELTA
            LOCATION '{silver_path}/products'
            AS
            SELECT *,
                CASE
                    WHEN price < 50 THEN 'Budget-friendly'
                    WHEN price >= 50 AND price < 100 THEN 'Mid-range'
                    ELSE 'Premium'
                END AS price_category
            FROM parquet.`{bronze_path}/products`
""")

Out[9]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

### Silver Layer OrderLineItems
- Save as it is

In [0]:
display(spark.sql(f""" 
              SELECT *
               FROM parquet.`{bronze_path}/orderLineItems`
           """))

line_item_id order_id product_id quantity unit_price round(CAST(price AS DECIMAL(10,2)), 2) subtotal ad8c4d56-42e3-4394-8adf-ff4ae6afe87d c948bce7-1791-44df-bba2-d41a00efcee2 3eecbb78-026d-49ca-a046-cfc8da76de81 9.0 140.01 140.01 1260.09 b372a930-8bb1-46c8-a131-f3b5e22a8ad1 58ceb347-da7a-40c9-befe-304fd6d500d7 81d49546-a209-4172-9069-0537cdde8a3e 7.0 428.84 428.84 3001.88 c1407ef6-65b8-4101-9810-da8762352cb7 f8e798e4-7200-44e0-a013-437177feddc7 5cde43fb-117e-4856-be15-ae87e6073d78 4.0 29.59 29.59 118.36 e3c29b43-ec9b-4f94-9218-da6976cc3514 38af4818-c586-4abb-aa51-bd8f211f6c0a 05f53f51-36ff-441c-9a0b-84fdbd8b9065 3.0 304.92 304.92 914.76 95117e3a-ed8c-40d3-8107-1a194ba9facd 38af4818-c586-4abb-aa51-bd8f211f6c0a cc7b830a-a68d-4576-bf23-50ec850ddf88 2.0 351.56 351.56 703.12 a91c85a7-520a-4a52-ba6d-2e7ec8c4e754 ffd9df96-fb1e-4d6e-9c39-a5607f18aea4 432f78f5-45d3-4d93-876e-4430d3d1c7ee 10.0 313.02 313.02 3130.20 8fb4657e-840b-412d-ad47-18cb8daba161 156bc169-8e82-4cf9-ae81-c3b816cb19b2 2e21326d-754e-46c2-a058-28131283a29c 7.0 89.33 89.33 625.31 bb2ba0a5-87ca-43ee-b857-82e5ef0c4d73 873cde0c-92f8-4a32-8aca-4ee69baff8f9 33c97c68-11b4-4d17-a0fc-072c84607b1e 8.0 466.55 466.55 3732.40 7f51a628-54a6-423d-8a68-818ed28f2cbf a6d5836b-c10f-4cb5-a63c-7e47cbc51f51 365b29aa-ff2e-4ea6-b8a5-a85edb602d10 6.0 440.11 440.11 2640.66 40e2562e-d275-48e3-96a5-79365ab75d2c 43b2601d-f59c-4905-8e3c-e19a0cff0ac8 0c4dcb34-a2d7-414b-9e2c-88f1d1058771 8.0 78.32 78.32 626.56 d1f735d2-ecfe-4606-861e-8b64e9a7d1d6 f2fb7f0d-3b8f-4e2d-ab56-ef0fe3d07532 a4a7d772-5d5d-492b-8934-38dd09f35def 7.0 388.86 388.86 2722.02 7422ff94-f9eb-41ef-8e3a-bde434b6f2d7 e0981783-097a-40ae-b2f6-611b64b069a5 610f76ea-551b-442b-9314-bed3a7ac9374 4.0 315.63 315.63 1262.52 ef499470-d6eb-4532-a2f7-53aa93dd3be4 87493839-7a61-4ce4-a360-80d1414cc383 a5954929-b0c5-4116-9cac-1d02801981fc 5.0 369.69 369.69 1848.45 1fc679ef-ac91-4b6e-bb62-10dbf7a6a6ec 5f850455-48ea-403e-af52-32b848c2f1c5 a8c73eac-9983-4491-bd28-0a42d90f2eb9 10.0 116.71 116.71 1167.10 7f1ad40c-35da-4989-9784-81a5678b0096 8f0066b1-78b2-448e-91e4-a12f76cf055b 30b6813d-f71d-45a1-9f18-9a0360a2bffd 2.0 297.38 297.38 594.76 118bd282-c9d0-43e7-bf36-15703ee266b1 0cd87450-6e70-45fd-bf4b-eb951731e1c6 40001f9c-ebdc-411d-9391-8cd14114b5b5 4.0 67.98 67.98 271.92 15da1da8-7e04-42d8-97b9-949a98519e26 73229bef-4ec8-4c81-9ee2-2c078d338c23 9866ba0b-cc07-47ef-a436-749266e91ff2 1.0 89.83 89.83 89.83 2d9fd369-00fb-4e61-8925-52d64ecabbcb bd3f0788-e75a-4356-99e4-c3359f5ea0b9 74fda5e9-b512-4a9f-9e3c-2688091e8e8a 10.0 488.45 488.45 4884.50 96eea6ba-a8b1-40bb-aa84-e184089772a7 53a79063-9b1b-4e82-99e1-9a2cf7e33a1e d0e0b96c-870f-4d6e-a31a-29577389b63f 8.0 86.63 86.63 693.04 84e844f1-bf66-48af-ac1f-17f739e2c070 00dcfa69-e9d0-43f8-89ff-fb01ccd30d78 f36a01af-2a1f-48d3-a29f-556056749934 4.0 467.20 467.20 1868.80 cc03ef12-705f-41d6-8ce3-073c8578a398 1cb1b9ec-3cad-4c5f-84d5-0513deab83b4 a8b5c2c4-b6c9-46f7-8828-272ccd89da55 7.0 34.10 34.10 238.70 f610d30b-8097-4fd9-bad7-0c1a64cbeb7d 6958074f-3327-4cc0-9639-b934828f60a0 a0f0a35a-c6f2-40db-a00d-e5ef2c6e00b6 2.0 433.80 433.80 867.60 11896af2-e7f7-498f-839c-6026177e4f87 4b606a1e-4b27-4f14-be64-f5b4c6bdd48e ba842fc9-dcf8-4e8f-b37e-a2ee796853ea 3.0 123.39 123.39 370.17 104f76d2-eb64-4641-a5c4-54a1aa88470b ec783e2c-fdc4-428d-8aa2-965a5b6656ec e3c70236-66ba-4dfd-ba10-68083907048f 3.0 279.80 279.80 839.40 4ad720be-19c6-47eb-baeb-47b1bf876a16 5ab754d6-f933-41ad-ac11-00ad1799b2be 9ccc0018-5bb9-4179-9a97-4fcf05fa637d 9.0 478.36 478.36 4305.24 535aca10-afe8-4973-8f3d-35a0848353d2 2b54af7a-199a-4798-a607-3babf3a6e724 d97bf2de-3d39-4012-afc3-96388b76c252 9.0 39.43 39.43 354.87 aec9350a-ead1-40a5-b7ed-0a5584e37758 c384a747-28a2-4024-8e51-439f19c5e95e 1b5e8ab9-04fe-411f-8b2b-536bc3ff307f 4.0 42.44 42.44 169.76 711084e1-5469-453c-847c-f21815b0d449 5781696f-2f74-4531-91b6-b6df5b3dbb63 22a9a9a4-9387-48e9-9e6b-f196aa5b0eca 6.0 203.27 203.27 1219.62 8ff2f68b-336f-4ec8-9baf-5277b3aa0df2 26b54653-5b41-41e5-aeb8-b3d79a1d9e21 256c1c28-4fe3-4956-a

In [0]:
spark.sql(f"""
        CREATE OR REPLACE TABLE silver_orderLineItems
        USING DELTA
        LOCATION '{silver_path}/orderLineItems'
        AS
        SELECT line_item_id, 
                order_id, 
                product_id,
                quantity,
                unit_price,
                subtotal
        FROM parquet.`{bronze_path}/orderLineItems`
""")

Out[11]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

### Silver Layer Orders

- Add an extra column to calculate 'Final Order Total'.

- Discount Amount will be applied on top of Order total only

- Order Total After Discount = (Order Total Before Discount) + Shipping Amount - Discount Amount

In [0]:
orders_df = spark.read.format('parquet') \
                      .load(bronze_path + '/orders/')

orders_df.createOrReplaceTempView('orders')

In [0]:
%sql

SELECT * FROM orders LIMIT 5

order_id total_amount num_items customer_id order_date status promotion_id payment_method shipping_cost shipping_address shipping_city shipping_state shipping_zip shipping_country 63bb4c9b-4cbb-4edb-8dac-9120b17262c5 10572.76 6 6b206779-58be-4934-bfeb-cad9a1cf3fb2 2025-02-06T04:15:40.826+0000 Pending 5ae39b31-e2a3-4f41-97ba-28239f6a5762 Cash on Delivery 48.40 7468 Barton Centers Port Jamesburgh Delaware 81695 United States ce46a768-b535-4c05-89a5-b5ca66314d80 89.55 1 f4445033-64d0-4505-b857-afbf38306fe4 2025-02-08T13:46:37.570+0000 Delivered 91527ba1-a6ac-48db-98c6-632573f3e4e0 PayPal 7.43 541 David Unions Suite 105 West Sarastad North Dakota 81388 United States 381bd206-a2f1-4d5b-a632-11a496a8b1bc 2853.55 3 05dcf61b-6646-475a-98d0-8a7a0786b3ea 2025-01-22T22:46:24.835+0000 Delivered 1a47f448-b65a-4174-8e26-169525a39e45 Cash on Delivery 24.36 719 Caleb Prairie Davidmouth Missouri 29972 United States 7a026552-5c94-4222-b394-ec73a8c46651 5364.98 2 c5a9ef30-48d3-4c5f-9c8b-28341239a062 2025-02-04T20:19:54.418+0000 Processing efbbe61f-05c0-4469-bf56-a6d326308e5b Credit Card 49.86 496 Barry Curve East Kylefurt Maine 64342 United States 3d232992-6e11-46ec-85f7-317792ba1ae7 5981.36 3 b33451da-7dfc-4082-8c49-34cf4c6b8043 2025-01-11T21:46:35.496+0000 Delivered c7ecb4b5-b0e7-423e-9888-0901a3cf53c7 PayPal 18.21 65631 Anderson Haven Apt. 984 North Cynthiaview North Dakota 42079 United States

In [0]:
orders_discount_applied_df = spark.sql(
                    
                        """
                            SELECT o.order_id,
                            o.customer_id,
                            o.promotion_id,
                            o.total_amount,
                            o.shipping_cost,
                            -- Creating discount amount column
                            CASE
                                WHEN p.discount_type = 'Percentage' THEN ROUND( (p.discount_value * o.total_amount) / 100, 2)
                                WHEN p.discount_type = 'Fixed Amount' THEN ROUND(p.discount_value, 2)
                            END AS discount_amount,

                            ROUND( (o.total_amount + o.shipping_cost - discount_amount), 2) AS order_total_after_discount,
                            o.num_items,
                            o.customer_id,
                            o.order_date,
                            o.status,
                            o.payment_method,
                            o.shipping_address, 
                            o.shipping_state, 
                            o.shipping_city, 
                            o.shipping_zip, 
                            o.shipping_country

                            FROM orders o
                            INNER JOIN silver_db.silver_promotions p
                            ON o.promotion_id = p.promotion_id
                        """
                    )


orders_discount_applied_df.createOrReplaceTempView("orders_discount_applied")

In [0]:
silver_orders_df = spark.sql(
                            """                
                                SELECT o.order_id,
                                    o.customer_id,
                                    c.first_name, c.last_name, c.email,
                                    o.promotion_id,
                                    o.total_amount AS subtotal,
                                    o.shipping_cost,
                                    o.discount_amount,
                                    o.order_total_after_discount,
                                    o.num_items,
                                    o.order_date,
                                    o.status,
                                    o.payment_method,
                                    o.shipping_address, 
                                    o.shipping_state, 
                                    o.shipping_city, 
                                    o.shipping_zip, 
                                    o.shipping_country
                                    
                                FROM orders_discount_applied o
                                INNER JOIN silver_db.silver_customers c
                                ON o.customer_id = c.customer_id
                            """
                            )

silver_orders_df.createOrReplaceTempView("silver_orders")

In [0]:
spark.sql(f"""
                CREATE OR REPLACE TABLE silver_orders
                USING DELTA
                LOCATION '{silver_path}/orders'
                AS
                
                SELECT * FROM silver_orders
        """)

Out[16]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
%sql

SELECT * FROM silver_orders LIMIT 10

order_id customer_id first_name last_name email promotion_id subtotal shipping_cost discount_amount order_total_after_discount num_items order_date status payment_method shipping_address shipping_state shipping_city shipping_zip shipping_country 63bb4c9b-4cbb-4edb-8dac-9120b17262c5 6b206779-58be-4934-bfeb-cad9a1cf3fb2 Lauren Greene ihudson@example.com 5ae39b31-e2a3-4f41-97ba-28239f6a5762 10572.76 48.40 3366.37 7254.79 6 2025-02-06T04:15:40.826+0000 Pending Cash on Delivery 7468 Barton Centers Delaware Port Jamesburgh 81695 United States ce46a768-b535-4c05-89a5-b5ca66314d80 f4445033-64d0-4505-b857-afbf38306fe4 Vanessa Miller diazsteven@example.org 91527ba1-a6ac-48db-98c6-632573f3e4e0 89.55 7.43 32.26 64.72 1 2025-02-08T13:46:37.570+0000 Delivered PayPal 541 David Unions Suite 105 North Dakota West Sarastad 81388 United States 381bd206-a2f1-4d5b-a632-11a496a8b1bc 05dcf61b-6646-475a-98d0-8a7a0786b3ea Daniel Freeman whitecolleen@example.com 1a47f448-b65a-4174-8e26-169525a39e45 2853.55 24.36 46.72 2831.19 3 2025-01-22T22:46:24.835+0000 Delivered Cash on Delivery 719 Caleb Prairie Missouri Davidmouth 29972 United States 7a026552-5c94-4222-b394-ec73a8c46651 c5a9ef30-48d3-4c5f-9c8b-28341239a062 Gregory Jenkins nlam@example.net efbbe61f-05c0-4469-bf56-a6d326308e5b 5364.98 49.86 2557.49 2857.35 2 2025-02-04T20:19:54.418+0000 Processing Credit Card 496 Barry Curve Maine East Kylefurt 64342 United States 3d232992-6e11-46ec-85f7-317792ba1ae7 b33451da-7dfc-4082-8c49-34cf4c6b8043 Dawn Barnes hurstmichael@example.net c7ecb4b5-b0e7-423e-9888-0901a3cf53c7 5981.36 18.21 1991.79 4007.78 3 2025-01-11T21:46:35.496+0000 Delivered PayPal 65631 Anderson Haven Apt. 984 North Dakota North Cynthiaview 42079 United States 057292ce-a74f-480b-96af-60cdc5f6861f 5a2d208a-67e5-4abe-9900-dd6c0e60c211 Wesley Francis msanchez@example.net d33c23ca-0910-482a-89d0-a424bd7ee7c9 4353.53 6.88 1152.81 3207.60 2 2025-01-05T13:37:31.054+0000 Shipped Cash on Delivery 362 Neal Ford Suite 751 Illinois West Nicholasshire 62890 United States bfbd20a2-7173-4f39-8fc9-8b5e9ae9befc 12b624ad-5a5b-4db5-9d4a-36eeeac584e8 Caitlin Dawson yangaustin@example.org c64d1257-2e50-4f0a-9841-28608abdd77e 1533.60 31.79 706.38 859.01 1 2025-02-09T10:21:27.203+0000 Cancelled Invalid 99134 Moore Knolls North Carolina Patrickton 36528 United States 32bc10b9-65c4-43f5-a815-7b06132e82de 5978e784-35c6-450b-b6b7-006f52529465 Jerry Kelley sarah34@example.net 3442db3f-c89b-4909-8d1f-63db334aa6d5 1698.85 5.13 9.60 1694.38 3 2025-01-02T15:59:07.614+0000 Delivered Credit Card 98717 Pierce Cliff Texas Myersmouth 47849 United States a3158b18-7006-4514-b2ed-008feb0d6925 c8332515-08bd-4a77-bfeb-1bbdd0c56830 Megan Macdonald tiffanymiranda@example.net 5ae39b31-e2a3-4f41-97ba-28239f6a5762 6624.92 49.09 2109.37 4564.64 3 2025-01-20T22:44:49.226+0000 Pending Bank Transfer 477 Vasquez Unions Apt. 013 Alaska Port Tonya 42181 United States 81a81d4f-81a4-4c7f-9276-5570ef604352 eba67996-9ad4-42ca-ae5d-fc0a3820400f Carolyn Price tammy52@example.net db8c69a8-1797-4830-a58c-2350b67c6341 4217.14 34.45 42.73 4208.86 4 2025-01-17T14:36:42.432+0000 Cancelled Debit Card 620 Elizabeth Wall Ohio North Christina 10961 United States